# Weights

This section computes weight for major aircraft structural components, along with various miscellaneous weights, for the example airplane. The statistical equations used below are referenced from different books (source is mentioned in each sub-section). For brevity, equations are not provided here. It is recommended to compare weights computed using statistical relations provided by different sources, and then select a sensible value. If possible, compare final weight values for each component with available data.

Below code block imports pacakges and defines some quantities used in various equations. The dynamic pressure is computed at cruise conditions (used in various equations). The limit load will be described in detail for V-n diagrams but for now it is set to 3.5.

In [50]:
import math

# Dynamic pressure
rho = 0.00186850 # slugs/cu ft, at 8000 ft
V = 337.562 # ft/s, 200 knots
q = 0.5*rho*V**2 # lbs/sq ft dynamic pressure at cruise

Wdg = 5354 # lbs, MTOW
Wfw = 1060 # lbs, fuel weight
avgas_density = 6.41 # lbs/gallon at -40 C

Nz = 1.5 * 3.5 # limit load factor is set to 3.5

## Wing

The wing weight is computed using Raymer equation 15.46 which takes into account wing planform parameters and other variables. One can also compute wing weight using Roskam part 5 equation 5.2 or 5.4.

Below code block computes wing weight:

In [ ]:
Sw = 134 # sq ft
A = 8
taper_ratio = 0.4
tc = 0.16 # average tc for the wing section between root and mac
sweep = 0 # quarter chord sweep
wing_span = 33 # ft

Wwing = 0.036*Sw**0.758 * Wfw**0.0035 * (A/math.cos(sweep)**2)**0.6 * q**0.006 * taper_ratio**0.04 \
        * (100*tc/math.cos(sweep))**-0.3 * (Nz*Wdg)**0.49

print(f"Weight of the wing: {Wwing:.0f} lbs")

Weight of the wing: 344 lbs


## Fuselage

The fuselage weight is computed using Raymer equation 15.49 but one can also compute it using Roskam part equation 5.23 or 5.25.

Below code block computes fuselage weight:

In [ ]:
Sf = 380.12 # sq ft, fuselage wetted from openvsp
D = 1.5/12 # ft, structural depth
L = 27 # ft, structural length without nose and tail cap
Lt = 16 # ft, tail moment arm

Wfuselage = 0.052 * Sf**1.086 * (Nz*Wdg)**0.177 * Lt**(-0.051) * (L/D)**(-0.072) * q**0.241

print(f"Weight of the fuselage: {Wfuselage:.0f} lbs")

Weight of the fuselage: 367 lbs


## Tail

The horizontal and vertical tail weights are computed using Raymer equation 15.47 and 15.48. One can also use Roskam Part 5 Section 5.2 for computing empennage weights.

Below code block computes weight of the horizontal tail:

In [ ]:
Sht = 31 # sq ft
sweep_ht = 10 # deg
taper_ratio_ht = 0.741

Wht = 0.016 * (Nz*Wdg)**0.414 * q**0.168 * Sht**0.896 * (100*tc/math.cos(sweep*math.pi/180))**-0.12 \
        * (A/math.cos(sweep_ht*math.pi/180)**2)**0.043 * taper_ratio_ht**-0.02

print(f"Weight of the HT: {Wht:.0f} lbs")

Weight of the HT: 42 lbs


Below code block computes weight of the vertical tail:

In [60]:
Svt = 17 # sq ft
taper_ratio_vt = 0.55
sweep_vt = 30 # deg
tail_factor = 0 # 0.0 for conv tail

Wvt = 0.073 * (1+0.2*tail_factor) * (Nz*Wdg)**0.376 * q**0.122 * Svt**0.873 \
        * (100*tc/math.cos(sweep_vt*math.pi/180))**-0.49 * (A/math.cos(sweep_vt*math.pi/180)**2)**0.357 \
        * taper_ratio_vt**0.039

print(f"Weight of the VT: {Wvt:.0f} lbs")

Weight of the VT: 39 lbs


## Landing Gear

The landing gear (LG) weight is computed using equation 5.4 in Roskam Part 5. The ultimate landing load factor is 1.5 times the gear load factor which is set to 3 using Table 11.5 in Raymer. The main LG extended length is estimate based on propeller diameter and required clearance. The propeller radius of 2.9 ft and 1.1 ft clerance leads to an approximate extended length of 4 ft. Note that for the example airplane, the LG is mounted close to engine mounts and retracted into wings. The value obtained is the total LG weight, including nose LG. Later, it is assumed that nose LG is 25% of the total LG weight.

In [ ]:
Ngear = 3 # from Table 11.5
Nl = 1.5 * Ngear
WL = 0.95*Wdg
Lm = 4 # ft

Wlg = 0.054 * Lm**0.501 * (WL*Nl)**0.684

print(f"Weight of the total LG: {Wlg:.0f} lbs")
print(f"Weight of the Main LG: {0.75*Wlg:.0f} lbs")
print(f"Weight of the Nose LG: {0.25*Wlg:.0f} lbs")

Weight of the total LG: 104 lbs
Weight of the Main LG: 78 lbs
Weight of the Nose LG: 26 lbs


## Propulsion system

The installed engine weight is computed using equation 15.52 in Raymer. As described in propulsion section, the Continental IO-550-N engine is going to be used for example airplane. The fuel systems weight is computed using equation 15.53.

Below code block computes installed engine and fuel systems weight:

In [61]:
Wen = 491 # lbs
Nen = 2

Winst_eng = 2.575 * Wen**0.922 * Nen

print(f"Weight of the installed engine: {Winst_eng:.0f} lbs")

Vt = Wfw / avgas_density
Vi = Vt
Nt = 2 # number of fuel tanks

Wfuel_system = 2.49 * Vt**0.726 * (1 + Vi/Vt)**-0.363 * Nt**0.242 * Nen**0.157

print(f"Weight of the fuel systems: {Wfuel_system:.0f} lbs")

Weight of the installed engine: 1559 lbs
Weight of the fuel systems: 104 lbs


## Miscellaneous

There are many other fixed components whose weight needs to be estimated such as flight controls, hydraulics, avionics, etc. The equations are referenced from different books, refer comments in below code block for the source. Note that the weights for anti-icing, pressurization, and air conditioning are not included.

In [65]:
# flight controls
Wflight_controls = 0.0168 * Wdg # Roskam Part 5, equation 7.2

# hydraulics
M = 0.3 # cruise mach number
Kh = 0.05 # low subsonic with hydraulics for brakes and retracts only
Whydraulics = Kh * Wdg**0.8 * M**0.5 # Raymer, equation 15.55

# avionics
Wavionics = 40 + 0.008 * Wdg # Roskam Part 5, 7.23

# electrical
Welectrical = 0.0268 * Wdg # Roskam Part 5, 7.13

# furshings
Wfurshings = 0.412 * 6**1.145 * Wdg**0.489 # Roskam Part 5, 7.41

print(f"Weight of the flight controls: {Wflight_controls:.0f} lbs")
print(f"Weight of the hydraulics: {Whydraulics:.0f} lbs")
print(f"Weight of the avionics: {Wavionics:.0f} lbs")
print(f"Weight of the electrical: {Welectrical:.0f} lbs")
print(f"Weight of the furshings: {Wfurshings:.0f} lbs")
print(f"Total miscellaneous weights: {Wflight_controls+Whydraulics+Wavionics+Welectrical+Wfurshings:.0f} lbs")

Weight of the flight controls: 90 lbs
Weight of the hydraulics: 26 lbs
Weight of the avionics: 83 lbs
Weight of the electrical: 143 lbs
Weight of the furshings: 213 lbs
Total miscellaneous weights: 556 lbs


## Summary

Following table summarizes the weights computed in this section:

<div style="width:40%; margin: auto;">

Component | Weight (lbs) 
 --- | :----:
Wing | 344
Fuselage | 367
Horizontal tail | 42
Vertical tail | 39
Main LG | 78
Nose LG | 26
Installed engine | 1559
Fuel systems | 104
Flight controls | 90 
Hydraulics | 26
Avionics | 83
Electrical | 143
Furshings | 213
**Total Empty weight** | 3114

</div>

> __*NOTE*__: The value obtained here (3114 lbs) is close to what was obtained earlier in empty weight estimation (3094 lbs).

This concludes the weights section. Next step is to compute the CG and plot CG travel diagram.